In [1]:
#import urllib2
import requests
from bs4 import BeautifulSoup
import re
from os.path import exists, expanduser
from os import makedirs
import pandas as pd
import numpy as np
import re

In [2]:
def pull_results(Bsoup):
    clean = []
    pull = Bsoup.findAll('span', attrs={'class': re.compile("icon(.*?)square")})

    # Clean to make useable 
    for i in pull:
        if 'minus' in str(i): 
            clean.append('loss')
        elif 'plus' in str(i): 
            clean.append('win')
        elif 'equal' in str(i):
            clean.append('draw')
        else:
            clean.append('error')
    
    return clean

In [3]:
def pull_moves(Bsoup):
    moves = []
    for i in Bsoup.findAll('td', attrs={'class': re.compile("table-text-center")}):
        if i.find('span'):
            moves.append(int(i.find('span').text))
    
    return moves

In [4]:
def pull_dates(Bsoup):
    dates = []
    for i in Bsoup.findAll('td', attrs={'class': re.compile("table-text-right archive-games-date-cell")}):
        dates.append(i.getText().strip())
    
    return dates

In [5]:
def pull_speed(Bsoup):
    times = []
    for i in b.findAll('span', attrs={'class': re.compile("archive-games-game-time")}):
        times.append((i.getText().strip()))
    
    return times

In [6]:
def remove_dups(duplicate): 
    final_list = [] 
    for num in duplicate: 
        if num not in final_list: 
            final_list.append(num) 
    return final_list

In [7]:
def pull_game_links(Bsoup):
    links = []
    for i in b.findAll('td', attrs={'class': re.compile("table-text-center archive-games-analyze-cell")}):
        for j in i.findAll('a'):
            links.append(j.get('href'))
                        
    return remove_dups(links)

In [8]:
def find_color(text):
    if 'white' in str(text):
        return 'white'
    elif 'black' in str(text):
        return 'black'
    else:
        return 'error'

In [9]:
def pull_player_stats(Bsoup):
    my_elo_lst = []
    opponent_elo_lst = []
    opponent_country_lst = []
    opponent_name_lst = []
    my_color_lst = []
    for cell in b.findAll('td', {'class':'archive-games-user-cell'}):
        # Split the halves
        top_half = cell.findAll('div', {'class': 'post-view-meta-user'})[0]
        bottom_half = cell.findAll('div', {'class': 'post-view-meta-user'})[1]
        
        top_color = find_color(cell.findAll('span')[0])
        bottom_color = find_color(cell.findAll('span')[2])
        
        # Logic to see if I'm top player or bottom player
        if top_half.text.strip().split('\n')[0] == 'Jayjay1988':
            my_elo= top_half.find('span', {'class':'post-view-meta-rating'}).text
            my_color= top_color
            opponent_elo = bottom_half.find('span', {'class':'post-view-meta-rating'}).text
            opponent_country = bottom_half.find('div').get('v-tooltip')
            opponent_name = bottom_half.text.strip().split('\n')[0]
        else: 
            my_elo= bottom_half.find('span', {'class':'post-view-meta-rating'}).text
            my_color= bottom_color
            opponent_elo = top_half.find('span', {'class':'post-view-meta-rating'}).text
            opponent_country = top_half.find('div').get('v-tooltip')
            opponent_name = top_half.text.strip().split('\n')[0]        
        
        # Clean
        my_elo = int(my_elo.replace('(','').replace(')', ''))
        opponent_elo = int(opponent_elo.replace('(','').replace(')', ''))
        opponent_country = opponent_country.replace("'", "")
        
        # Gather data 
        my_elo_lst.append(my_elo)
        my_color_lst.append(my_color)
        opponent_elo_lst.append(opponent_elo)
        opponent_country_lst.append(opponent_country)
        opponent_name_lst.append(opponent_name)

    return(my_elo_lst, opponent_elo_lst, opponent_country_lst, opponent_name_lst, my_color_lst)

In [10]:


# Initialize lists
results = []
moves = []
dates = []
speed = []
games = []
my_elo = []
my_color = []
opponent_elo = []
opponent_country = []
opponent_name = []

for i in range(1,17):
    # Get the page
    text = requests.get("""https://www.chess.com/games/archive/Jayjay1988?show=live_blitz&gameType=live_blitz&rated=rated&page={}""".format(i)).text
    # Soupify
    b = BeautifulSoup(text, 'html.parser')
    #print(b)
    # Collect results
    results += pull_results(b)
    moves += pull_moves(b)
    dates += pull_dates(b)
    speed += pull_speed(b)
    games += pull_game_links(b)
    my_elo += pull_player_stats(b)[0]
    opponent_elo += pull_player_stats(b)[1]
    opponent_country += pull_player_stats(b)[2]
    opponent_name += pull_player_stats(b)[3]
    my_color += pull_player_stats(b)[4]
    
    
# Make Df
d = {'date': dates,
     'result': results,
     'moves': moves,
     'speed': speed,
     'link': games,
     'my_elo': my_elo,
     'opponent_elo': opponent_elo,
     'opponent_country': opponent_country,
     'opponent_name': opponent_name,
     'color': my_color
}



games_df = pd.DataFrame(d)

In [11]:

# Initialize lists
results = []
moves = []
dates = []
speed = []
games = []
my_elo = []
my_color = []
opponent_elo = []
opponent_country = []
opponent_name = []

for i in range(1,14):
    # Get the page
    text = requests.get("""https://www.chess.com/games/archive/Jayjay1988?show=live_lightning&gameType=live_lightning&rated=rated&page={}""".format(i)).text
    # Soupify
    b = BeautifulSoup(text, 'html.parser')
    #print(b)
    # Collect results
    results += pull_results(b)
    moves += pull_moves(b)
    dates += pull_dates(b)
    speed += pull_speed(b)
    games += pull_game_links(b)
    my_elo += pull_player_stats(b)[0]
    opponent_elo += pull_player_stats(b)[1]
    opponent_country += pull_player_stats(b)[2]
    opponent_name += pull_player_stats(b)[3]
    my_color += pull_player_stats(b)[4]
    
    
# Make Df
d = {'date': dates,
     'result': results,
     'moves': moves,
     'speed': speed,
     'link': games,
     'my_elo': my_elo,
     'opponent_elo': opponent_elo,
     'opponent_country': opponent_country,
     'opponent_name': opponent_name,
     'color': my_color
}



games_df_bullet = pd.DataFrame(d)

In [12]:
games_df['scrape_key']=games_df['link']


In [13]:
games_df_bullet['scrape_key']=games_df_bullet['link']

In [14]:
for i in range(len(games_df)):
    games_df.loc[i,'scrape_key']=re.search('(\d+)', games_df['link'][i]).group(1)
    

In [15]:
for i in range(len(games_df_bullet)):
    games_df_bullet.loc[i,'scrape_key']=re.search('(\d+)', games_df_bullet['link'][i]).group(1)

In [16]:
games_df_dup=games_df

In [17]:
import datetime
games_df['date'] = pd.to_datetime(games_df['date'])
games_df['date'] = games_df['date'].dt.strftime('%m.%d.%Y')


In [18]:
import datetime
games_df_bullet['date'] = pd.to_datetime(games_df_bullet['date'])
games_df_bullet['date'] = games_df_bullet['date'].dt.strftime('%m.%d.%Y')

In [19]:
games_df=games_df[(games_df['date']>='01.01.2020') & (games_df['date']<='03.31.2020')]
games_df_bullet=games_df_bullet[(games_df_bullet['date']>='01.01.2020') & (games_df_bullet['date']<='03.31.2020')]
games_df

date result  moves   speed  \
5    03.25.2020    win     67  10 min   
6    03.25.2020   loss     27  10 min   
7    03.25.2020    win     37  10 min   
8    03.25.2020    win     67  10 min   
9    03.25.2020   loss     63  10 min   
..          ...    ...    ...     ...   
537  01.01.2020   loss     41  10 min   
538  01.01.2020   loss     12  10 min   
539  01.01.2020   loss     21  10 min   
540  01.01.2020   loss     56  10 min   
541  01.01.2020    win     33  10 min   

                                                  link  my_elo  opponent_elo  \
5    https://www.chess.com/analysis/game/live/46387...    1275          1197   
6    https://www.chess.com/analysis/game/live/46387...    1268          1185   
7    https://www.chess.com/analysis/game/live/46387...    1278          1184   
8    https://www.chess.com/analysis/game/live/46386...    1272          1200   
9    https://www.chess.com/analysis/game/live/46386...    1265          1211   
..                                                 ...     ...           ...   
537  https://www.chess.com/analysis/game/live/43559...    1210          1239   
538  https://www.chess.com/analysis/game/live/43559...    1218          1229   
539  https://www.chess.com/analysis/game/live/43559...    1226          1272   
540  https://www.chess.com/analysis/game/live/43558...    1233          1239   
541  https://www.chess.com/analysis/game/live/43552...    1241          1269   

    opponent_country  opponent_name  color  scrape_key  
5      International        Komodo9  error  4638721657  
6      International        Komodo9  white  4638713983  
7      International        Komodo9  error  4638707496  
8      International        Komodo9  white  4638693960  
9      International        Komodo9  error  4638678640  
..               ...            ...    ...         ...  
537            Egypt       KazaMeza  white  4355955582  
538           Russia    Andrew72962  black  4355949633  
539           Latvia      pavel-abc  black  4355929485  
540      Netherlands      ziggy1961  black  4355878508  
541      Isle of Man  jeffchakamata  white  4355214812  

[537 rows x 11 columns]

In [20]:
games_df_final=games_df.append(games_df_bullet)

In [21]:
games_df_final=games_df_final.reset_index()

In [22]:
games_df_final=games_df_final.rename(columns={"scrape_key": "Api_url_key"})

In [23]:
games_df_final

index        date result  moves   speed  \
0         5  03.25.2020    win     67  10 min   
1         6  03.25.2020   loss     27  10 min   
2         7  03.25.2020    win     37  10 min   
3         8  03.25.2020    win     67  10 min   
4         9  03.25.2020   loss     63  10 min   
...     ...         ...    ...    ...     ...   
1159    622  01.26.2020    win     14   1 min   
1160    623  01.26.2020   loss     27   1 min   
1161    624  01.26.2020   loss     25   1 min   
1162    625  01.26.2020   loss     24   1 min   
1163    626  01.26.2020   loss     14   1 min   

                                                   link  my_elo  opponent_elo  \
0     https://www.chess.com/analysis/game/live/46387...    1275          1197   
1     https://www.chess.com/analysis/game/live/46387...    1268          1185   
2     https://www.chess.com/analysis/game/live/46387...    1278          1184   
3     https://www.chess.com/analysis/game/live/46386...    1272          1200   
4     https://www.chess.com/analysis/game/live/46386...    1265          1211   
...                                                 ...     ...           ...   
1159  https://www.chess.com/analysis/game/live/44388...     456           335   
1160  https://www.chess.com/analysis/game/live/44388...     401           512   
1161  https://www.chess.com/analysis/game/live/44388...     467           548   
1162  https://www.chess.com/analysis/game/live/44388...     567           826   
1163  https://www.chess.com/analysis/game/live/44388...     631           821   

     opponent_country     opponent_name  color Api_url_key  
0       International           Komodo9  error  4638721657  
1       International           Komodo9  white  4638713983  
2       International           Komodo9  error  4638707496  
3       International           Komodo9  white  4638693960  
4       International           Komodo9  error  4638678640  
...               ...               ...    ...         ...  
1159            India          SUHEL786  white  4438859294  
1160    United States  FranklStankovich  white  4438854572  
1161    United States         Leibalove  black  4438850885  
1162           Israel          Genadyka  black  4438847032  
1163           Israel          Genadyka  white  4438845021  

[1164 rows x 12 columns]

In [24]:

text_01 = requests.get("https://api.chess.com/pub/player/jayjay1988/games/2020/01").text
# Soupify
a = BeautifulSoup(text_01, 'html.parser')
a=a.prettify()

In [25]:

text_02 = requests.get("https://api.chess.com/pub/player/jayjay1988/games/2020/02").text
# Soupify
b = BeautifulSoup(text_02, 'html.parser')
b=b.prettify()

In [26]:

text_03 = requests.get("https://api.chess.com/pub/player/jayjay1988/games/2020/03").text
# Soupify
c = BeautifulSoup(text_03, 'html.parser')
c=c.prettify()

In [27]:
import json
import pandas as pd

newDictionary_01=json.loads(str(a))
newDictionary_01




{'games': [{'url': 'https://www.chess.com/live/game/4355214812',
   'pgn': '[Event "Live Chess"]\n[Site "Chess.com"]\n[Date "2020.01.01"]\n[Round "-"]\n[White "Jayjay1988"]\n[Black "jeffchakamata"]\n[Result "1-0"]\n[ECO "B40"]\n[ECOUrl "https://www.chess.com/openings/Sicilian-Defense-French-Variation-3.d4"]\n[CurrentPosition "2r5/1Q4k1/4pnnp/3p4/p1B2Pp1/8/P5PP/3R2K1 b - -"]\n[Timezone "UTC"]\n[UTCDate "2020.01.01"]\n[UTCTime "08:50:07"]\n[WhiteElo "1241"]\n[BlackElo "1269"]\n[TimeControl "600"]\n[Termination "Jayjay1988 won by resignation"]\n[StartTime "08:50:07"]\n[EndDate "2020.01.01"]\n[EndTime "09:04:40"]\n[Link "https://www.chess.com/live/game/4355214812"]\n\n1. e4 {[%clk 0:09:59.9]} 1... e6 {[%clk 0:09:59.9]} 2. d4 {[%clk 0:09:58.5]} 2... c5 {[%clk 0:09:59.8]} 3. Nf3 {[%clk 0:09:54]} 3... cxd4 {[%clk 0:09:58.8]} 4. Nxd4 {[%clk 0:09:53]} 4... a6 {[%clk 0:09:57.4]} 5. Bc4 {[%clk 0:09:51.7]} 5... b5 {[%clk 0:09:56.1]} 6. Bb3 {[%clk 0:09:49.4]} 6... Bb7 {[%clk 0:09:48.8]} 7. Nc3 {[%c

In [28]:
import json
import pandas as pd

newDictionary_02=json.loads(str(b))
newDictionary_02['games'][1]

{'url': 'https://www.chess.com/live/game/4455132192',
 'pgn': '[Event "Live Chess"]\n[Site "Chess.com"]\n[Date "2020.02.01"]\n[Round "-"]\n[White "Jayjay1988"]\n[Black "nucciovalenti"]\n[Result "1-0"]\n[ECO "C00"]\n[ECOUrl "https://www.chess.com/openings/Pirc-Defense-Small-Center-Defense"]\n[CurrentPosition "3r2k1/5pp1/1q2pb1p/2B5/8/P4N2/5PPP/1RQ3K1 b - -"]\n[Timezone "UTC"]\n[UTCDate "2020.02.01"]\n[UTCTime "08:05:13"]\n[WhiteElo "1194"]\n[BlackElo "1175"]\n[TimeControl "600"]\n[Termination "Jayjay1988 won on time"]\n[StartTime "08:05:13"]\n[EndDate "2020.02.01"]\n[EndTime "08:24:55"]\n[Link "https://www.chess.com/live/game/4455132192"]\n\n1. e4 {[%clk 0:09:59.9]} 1... e6 {[%clk 0:09:59.3]} 2. d4 {[%clk 0:09:57.9]} 2... d6 {[%clk 0:09:58.8]} 3. Nf3 {[%clk 0:09:54.9]} 3... c6 {[%clk 0:09:56.7]} 4. c4 {[%clk 0:09:53]} 4... Be7 {[%clk 0:09:56.1]} 5. Be2 {[%clk 0:09:48.8]} 5... b6 {[%clk 0:09:55.5]} 6. Nc3 {[%clk 0:09:45.7]} 6... Ba6 {[%clk 0:09:54.8]} 7. O-O {[%clk 0:09:34.5]} 7... Nf6 {

In [29]:
import json
import pandas as pd

newDictionary_03=json.loads(str(c))
newDictionary_03['games'][1]

{'url': 'https://www.chess.com/live/game/4552576071',
 'pgn': '[Event "Live Chess"]\n[Site "Chess.com"]\n[Date "2020.03.02"]\n[Round "-"]\n[White "Jayjay1988"]\n[Black "Atlant81"]\n[Result "1-0"]\n[ECO "C41"]\n[ECOUrl "https://www.chess.com/openings/Philidor-Defense"]\n[CurrentPosition "8/8/8/p1p4B/1b6/3Q3P/k3Q1K1/1R6 b - -"]\n[Timezone "UTC"]\n[UTCDate "2020.03.02"]\n[UTCTime "05:30:47"]\n[WhiteElo "1300"]\n[BlackElo "1090"]\n[TimeControl "600"]\n[Termination "Jayjay1988 won by resignation"]\n[StartTime "05:30:47"]\n[EndDate "2020.03.02"]\n[EndTime "05:43:15"]\n[Link "https://www.chess.com/live/game/4552576071"]\n\n1. e4 {[%clk 0:09:59.9]} 1... e5 {[%clk 0:09:58.5]} 2. Nf3 {[%clk 0:09:58]} 2... d6 {[%clk 0:09:57.5]} 3. h3 {[%clk 0:09:42.7]} 3... f5 {[%clk 0:09:56.1]} 4. d4 {[%clk 0:09:27.3]} 4... exd4 {[%clk 0:09:51.4]} 5. Nxd4 {[%clk 0:09:25.3]} 5... fxe4 {[%clk 0:09:50.1]} 6. Bc4 {[%clk 0:08:55.8]} 6... d5 {[%clk 0:09:35.1]} 7. Bb3 {[%clk 0:08:53.5]} 7... c6 {[%clk 0:09:33.1]} 8. Qh

In [30]:
newDictionary_final = {}
for i in range(len(newDictionary_01['games'])):
    print(i)
    k=newDictionary_01['games'][i]
    newDictionary_final.setdefault('games', [])
    newDictionary_final['games'].append(k)


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [31]:
for i in range(len(newDictionary_02['games'])):
    print(i)
    k=newDictionary_02['games'][i]
    newDictionary_final['games'].append(k)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94


In [32]:
for i in range(len(newDictionary_03['games'])):
    print(i)
    k=newDictionary_03['games'][i]
    newDictionary_final['games'].append(k)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [33]:
newDictionary_final

{'games': [{'url': 'https://www.chess.com/live/game/4355214812',
   'pgn': '[Event "Live Chess"]\n[Site "Chess.com"]\n[Date "2020.01.01"]\n[Round "-"]\n[White "Jayjay1988"]\n[Black "jeffchakamata"]\n[Result "1-0"]\n[ECO "B40"]\n[ECOUrl "https://www.chess.com/openings/Sicilian-Defense-French-Variation-3.d4"]\n[CurrentPosition "2r5/1Q4k1/4pnnp/3p4/p1B2Pp1/8/P5PP/3R2K1 b - -"]\n[Timezone "UTC"]\n[UTCDate "2020.01.01"]\n[UTCTime "08:50:07"]\n[WhiteElo "1241"]\n[BlackElo "1269"]\n[TimeControl "600"]\n[Termination "Jayjay1988 won by resignation"]\n[StartTime "08:50:07"]\n[EndDate "2020.01.01"]\n[EndTime "09:04:40"]\n[Link "https://www.chess.com/live/game/4355214812"]\n\n1. e4 {[%clk 0:09:59.9]} 1... e6 {[%clk 0:09:59.9]} 2. d4 {[%clk 0:09:58.5]} 2... c5 {[%clk 0:09:59.8]} 3. Nf3 {[%clk 0:09:54]} 3... cxd4 {[%clk 0:09:58.8]} 4. Nxd4 {[%clk 0:09:53]} 4... a6 {[%clk 0:09:57.4]} 5. Bc4 {[%clk 0:09:51.7]} 5... b5 {[%clk 0:09:56.1]} 6. Bb3 {[%clk 0:09:49.4]} 6... Bb7 {[%clk 0:09:48.8]} 7. Nc3 {[%c

In [34]:
actual_stats= pd.DataFrame(columns=['Url','Game_type', 'White'])
actual_stats['Url']=np.nan
actual_stats['Url']=actual_stats['Url'].values.astype(str)
actual_stats['Game_type']=np.nan
actual_stats['Game_type']=actual_stats['Game_type'].values.astype(str)
actual_stats['White']=np.nan
actual_stats['White']=actual_stats['White'].values.astype(str)
actual_stats['Black']=np.nan
actual_stats['Black']=actual_stats['Black'].values.astype(str)
actual_stats['Api_url_key']=np.nan
actual_stats['Api_url_key']=actual_stats['Api_url_key'].values.astype(str)
actual_stats['Opening_variation']=np.nan
actual_stats['Opening_variation']=actual_stats['Opening_variation'].values.astype(str)
actual_stats['First_move']=np.nan
actual_stats['First_move']=actual_stats['First_move'].values.astype(str)
actual_stats['Second_move']=np.nan
actual_stats['Second_move']=actual_stats['Second_move'].values.astype(str)
actual_stats['Openings']=np.nan
actual_stats['Openings']=actual_stats['Openings'].values.astype(str)
actual_stats['My_color']=np.nan
actual_stats['My_color']=actual_stats['My_color'].values.astype(str)
actual_stats['My_detailed_result']=np.nan
actual_stats['My_detailed_result']=actual_stats['My_detailed_result'].values.astype(str)
actual_stats['Opponent_detailed_result']=np.nan
actual_stats['Opponent_detailed_result']=actual_stats['Opponent_detailed_result'].values.astype(str)
actual_stats['My_first_move']=np.nan
actual_stats['My_first_move']=actual_stats['My_first_move'].values.astype(str)
actual_stats['Start_time']=np.nan
actual_stats['Start_time']=actual_stats['Start_time'].values.astype(str)
actual_stats['End_time']=np.nan
actual_stats['End_time']=actual_stats['End_time'].values.astype(str)
actual_stats

Empty DataFrame
Columns: [Url, Game_type, White, Black, Api_url_key, Opening_variation, First_move, Second_move, Openings, My_color, My_detailed_result, Opponent_detailed_result, My_first_move, Start_time, End_time]
Index: []

In [35]:
# text=newDictionary_final['games'][5]['pgn'][550:2250]
# type(text)
# reg_new=re.search(r'[\r\n]+[1-9][1-9]\.(.*?)\{',text).group(1)
# reg_new_2=re.search(r'\}\s[1-9][1-9]\...(.*?)\{',text).group(1)
# print(reg_new)
# # print(reg_new_2)
# for i in range(len(newDictionary_final['games'])):
#     reg_ref_text=newDictionary_final['games'][i]['pgn'][150:750]
#     reg_ref_text
#     reg_ref_text=reg_ref_text.split('\n')
#     reg_ref_text_arr=reg_ref_text[9][10:20]
#     print(reg_ref_text_arr)

In [36]:
# #text1='ve/game/4552637064"]\n\n1. e4 {[%clk 0:02:59.9]} 1... e5 {[%clk 0:02:59.9]} 2. Nf3 {[%clk 0:02:58.3]} 2... Nc6 {[%clk 0:02:59.8]} 3. Bb5 {[%clk 0:02:57.7]} 3... Nf6 {[%clk 0:02:58.5]} 4. O-O {[%clk 0:02'  
# text2='.9]} 1... e5 {[%clk 0:02:59.9]} 2. Nf3 {[%clk 0:02:58.3]} 2...'
# text3='kka} 1... e5 {' 
# reg_new=re.search(r'\}\s[1]\...(.*?)\{',text3).group(1)
# print(reg_new)


In [37]:
# reg_ref_text=newDictionary_final['games'][i]['pgn'][150:750]
# print(reg_ref_text)
# reg_ref_text_start=re.search(r'StartTime\s\"(.*?)"', reg_ref_text).group(1)
# reg_ref_text_end=re.search(r'EndTime\s\"(.*?)"', reg_ref_text).group(1)
# reg_ref_text_start

In [38]:
for i in range(len(newDictionary_final['games'])):
    actual_stats.loc[i,'Url']=newDictionary_final['games'][i]['url']
    actual_stats.loc[i,'Game_type']=newDictionary_final['games'][i]['time_class']
    actual_stats.loc[i,'Game_type']=newDictionary_final['games'][i]['time_class']
    actual_stats.loc[i,'White']=newDictionary_final['games'][i]['white']['result']
    actual_stats.loc[i,'Black']=newDictionary_final['games'][i]['black']['result']
    actual_stats.loc[i,'Api_url_key']=newDictionary_final['games'][i]['url'][32:42]
    
    
    

In [39]:
actual_stats

Url Game_type       White  \
0     https://www.chess.com/live/game/4355214812     blitz         win   
1     https://www.chess.com/live/game/4355878508     blitz         win   
2     https://www.chess.com/live/game/4355929485     blitz         win   
3     https://www.chess.com/live/game/4355949633     blitz         win   
4     https://www.chess.com/live/game/4355955582     blitz  checkmated   
...                                          ...       ...         ...   
1163  https://www.chess.com/live/game/4638721657     blitz  checkmated   
1164  https://www.chess.com/live/game/4638748558    bullet  repetition   
1165  https://www.chess.com/live/game/4638752154    bullet     timeout   
1166  https://www.chess.com/live/game/4651125308    bullet    resigned   
1167  https://www.chess.com/live/game/4651127864    bullet         win   

           Black Api_url_key Opening_variation First_move Second_move  \
0       resigned  4355214812               NaN        NaN         NaN   
1     checkmated  4355878508               NaN        NaN         NaN   
2       resigned  4355929485               NaN        NaN         NaN   
3       resigned  4355949633               NaN        NaN         NaN   
4            win  4355955582               NaN        NaN         NaN   
...          ...         ...               ...        ...         ...   
1163         win  4638721657               NaN        NaN         NaN   
1164  repetition  4638748558               NaN        NaN         NaN   
1165         win  4638752154               NaN        NaN         NaN   
1166         win  4651125308               NaN        NaN         NaN   
1167     timeout  4651127864               NaN        NaN         NaN   

     Openings My_color My_detailed_result Opponent_detailed_result  \
0         NaN      NaN                NaN                      NaN   
1         NaN      NaN                NaN                      NaN   
2         NaN      NaN                NaN                      NaN   
3         NaN      NaN                NaN                      NaN   
4         NaN      NaN                NaN                      NaN   
...       ...      ...                ...                      ...   
1163      NaN      NaN                NaN                      NaN   
1164      NaN      NaN                NaN                      NaN   
1165      NaN      NaN                NaN                      NaN   
1166      NaN      NaN                NaN                      NaN   
1167      NaN      NaN                NaN                      NaN   

     My_first_move Start_time End_time  
0              NaN        NaN      NaN  
1              NaN        NaN      NaN  
2              NaN        NaN      NaN  
3              NaN        NaN      NaN  
4              NaN        NaN      NaN  
...            ...        ...      ...  
1163           NaN        NaN      NaN  
1164           NaN        NaN      NaN  
1165           NaN        NaN      NaN  
1166           NaN        NaN      NaN  
1167           NaN        NaN      NaN  

[1168 rows x 15 columns]

In [40]:
for i in range(len(actual_stats)):
    try:
        actual_stats['First_move'][i]=re.search(r'[\r\n]+[1]\.(.*?)\{',newDictionary_final['games'][i]['pgn'][490:750]).group(1)
        actual_stats['Second_move'][i]=reg_new_2=re.search(r'\}\s[1]\...(.*?)\{',newDictionary_final['games'][i]['pgn'][490:750]).group(1)
        print(actual_stats['First_move'][i],i)
        print(actual_stats['Second_move'][i],i)
    except:
        actual_stats['First_move'][i]=None
        actual_stats['Second_move'][i]=None

 e4  0
 e6  0
 d4  1
 e6  1
 e4  2
 c5  2
 e4  3
 c5  3
 e4  4
 d5  4
 e4  5
 c5  5
 e4  6
 c5  6
 e4  7
 e6  7
 e3  8
 e5  8
 e4  9
 d5  9
 e4  10
 c5  10
 e4  11
 c5  11
 e4  12
 e5  12
 a3  13
 e5  13
 e4  14
 c6  14
 e4  15
 c5  15
 e4  16
 c5  16
 e4  17
 e5  17
 e4  18
 c5  18
 e4  19
 c5  19
 e4  20
 e5  20
 e4  21
 c5  21
 e4  22
 e5  22
 e4  23
 c5  23
 e4  24
 e5  24
 e4  25
 e5  25
 e4  26
 c5  26
 e4  27
 e5  27
 e4  28
 c5  28
 e4  29
 c5  29
 g4  30
 e5  30
 e4  31
 e5  31
 e3  32
 e5  32
 e4  33
 e6  33
 e3  34
 e5  34
 e4  35
 c5  35
 e4  36
 d6  36
 e4  37
 e5  37
 e4  38
 e5  38
 e4  39
 c5  39
 d4  40
 e6  40
 e4  41
 e5  41
 e4  42
 c6  42
 e4  43
 e5  43
 b3  44
 e5  44
 e4  45
 d5  45
 e4  46
 e5  46
 e4  47
 g6  47
 e4  48
 c5  48
 e4  49
 e5  49
 e4  50
 c5  50
 e3  51
 e5  51
 e4  52
 e5  52
 e4  53
 c5  53
 e4  54
 d5  54
 e4  55
 c5  55
 e4  56
 e5  56
 d4  57
 e6  57
 e4  58
 e5  58
 e4  59
 e6  59
 e4  60
 c5  60
 e4  61
 c5  61
 d4  62
 e6  62
 e4  63
 e5 

In [41]:
for i in range(len(actual_stats)):
    try:
        actual_stats['Opening_variation'][i]=re.search('openings/(.*)"]',newDictionary_final['games'][i]['pgn'][160:300]).group(1)
    except:
        actual_stats['Opening_variation'][i]=None

In [42]:
for i in range(len(actual_stats)):
    try:
        actual_stats['Start_time'][i]=re.search(r'StartTime\s\"(.*?)"', newDictionary_final['games'][i]['pgn'][150:750]).group(1)
        actual_stats['End_time'][i]=re.search(r'EndTime\s\"(.*?)"', newDictionary_final['games'][i]['pgn'][150:750]).group(1)
    except:
        actual_stats['Start_time'][i]=None
        actual_stats['End_time'][i]=None
    

In [43]:
ref_list=['Modern-Defense',
'Caro-Kann-Defense',
'Vienna-Game',
'Vant-Kruijs-Opening',
'Ruy-Lopez-Opening',
'Queens-Pawn-Opening',
'Indian-Game',
'Bishops-Opening',
'English-Opening',
'Nimzo-Indian-Defense',
'Sicilian-Defense',
'Torre-Attack-Fianchetto-Defense',
'Slav-Defense',
'Giuoco-Piano-Game',
'Alekhines-Defense',
'Queens-Gambit-Declined',
'Kings-Indian-Defense',
'Kings-Indian-Attack',
'Old-Benoni-Defense',
'Kings-Fianchetto-Opening',
'Scandinavian-Defense',
'Scotch-Game',
'Grob-Opening',
'London-System',
'Nimzowitsch-Larsen-Attack',
'French-Defense',
'Colle-System',
'Trompowsky-Attack',
'Grunfeld-Defense',
'Reti-Opening',
'Kadas-Opening',
'Pirc-Defense',
'Kings-Pawn-Opening',
'Englund-Gambit',
'Ponziani-Opening',
'Petrovs-Defense',
'Philidor-Defense',
'Kings-Gambit-Declined',
'Dutch-Defense',
'Birds-Opening',
'Three-Knights-Opening',
'Nimzowitsch-Defense',
'Italian-Game',
'English-Defense',
'Polish-Opening',
'Mieses-Opening',
'Catalan-Opening',
'Benoni-Defense',
'Benko-Gambit',
'Four-Knights-Game',
'Anderssen-Opening']








In [44]:
for i in range(len(actual_stats)):
    for j in ref_list:
        try:
            if j in actual_stats.at[i,'Opening_variation']:
                actual_stats.loc[i,'Openings']=j
                print(i,actual_stats.at[i,'Openings'],j)
        except:
                actual_stats.at[i,'Openings']=np.nan


0 Sicilian-Defense Sicilian-Defense
1 Indian-Game Indian-Game
2 Sicilian-Defense Sicilian-Defense
3 Sicilian-Defense Sicilian-Defense
4 Scandinavian-Defense Scandinavian-Defense
5 Sicilian-Defense Sicilian-Defense
6 Sicilian-Defense Sicilian-Defense
7 French-Defense French-Defense
8 Vant-Kruijs-Opening Vant-Kruijs-Opening
9 Scandinavian-Defense Scandinavian-Defense
10 Sicilian-Defense Sicilian-Defense
11 Sicilian-Defense Sicilian-Defense
12 Kings-Pawn-Opening Kings-Pawn-Opening
13 Anderssen-Opening Anderssen-Opening
14 Caro-Kann-Defense Caro-Kann-Defense
15 Sicilian-Defense Sicilian-Defense
16 Sicilian-Defense Sicilian-Defense
17 Ruy-Lopez-Opening Ruy-Lopez-Opening
18 Sicilian-Defense Sicilian-Defense
19 Sicilian-Defense Sicilian-Defense
20 Philidor-Defense Philidor-Defense
21 Sicilian-Defense Sicilian-Defense
22 Philidor-Defense Philidor-Defense
23 Sicilian-Defense Sicilian-Defense
24 Philidor-Defense Philidor-Defense
25 Scotch-Game Scotch-Game
26 Sicilian-Defense Sicilian-Defense
27 

In [45]:
for i in range(len(actual_stats)):
    text_black=newDictionary_final['games'][i]['black']['username']
    text_white=newDictionary_final['games'][i]['white']['username']
    if text_black == 'Jayjay1988':
        actual_stats.loc[i,'My_color']='black'
    else:
        actual_stats.loc[i,'My_color']='white'


In [46]:
for i in range(len(actual_stats)):
    if actual_stats.loc[i,'My_color']=='white':
        actual_stats.loc[i,'My_detailed_result']=actual_stats['White'][i]
        actual_stats.loc[i,'Opponent_detailed_result']=actual_stats['Black'][i]
    else:
        actual_stats.loc[i,'My_detailed_result']=actual_stats['Black'][i]
        actual_stats.loc[i,'Opponent_detailed_result']=actual_stats['White'][i]
        


In [47]:
for i in range(len(actual_stats)):
    if actual_stats.loc[i,'My_color']=='white':
        actual_stats.loc[i,'My_first_move']=actual_stats['First_move'][i]
    else:
        actual_stats.loc[i,'My_first_move']=actual_stats['Second_move'][i]


In [48]:
for i in range(len(actual_stats)):
            print(actual_stats['Openings'][i],actual_stats['Opening_variation'][i])

Sicilian-Defense Sicilian-Defense-French-Variation-3.d4
Indian-Game Indian-Game-East-Indian-Defense
Sicilian-Defense Sicilian-Defense-Closed-2...d6
Sicilian-Defense Sicilian-Defense-Smith-Morra-Gambit-Accepted-4.Nxc3-Nc6-5.Nf3-e6
Scandinavian-Defense Scandinavian-Defense-Mieses-Kotrc-Variation-3.Nc3
Sicilian-Defense Sicilian-Defense-Bowdler-Attack
Sicilian-Defense Sicilian-Defense-2.Nf3-d6
French-Defense French-Defense-St-George-Defense-3.Nf3
Vant-Kruijs-Opening Vant-Kruijs-Opening-1...e5
Scandinavian-Defense Scandinavian-Defense-Mieses-Kotrc-Gubinsky-Melts-Defense
Sicilian-Defense Sicilian-Defense-2.Nf3
Sicilian-Defense Sicilian-Defense-Open-3...cxd4-4.Nxd4
Kings-Pawn-Opening Kings-Pawn-Opening-Kings-Knight-Variation-2...Nc6
Anderssen-Opening Anderssen-Opening-1...e5
Caro-Kann-Defense Caro-Kann-Defense-2.d4
Sicilian-Defense Sicilian-Defense-2.Nf3-d6
Sicilian-Defense Sicilian-Defense-Open-Variation
Ruy-Lopez-Opening Ruy-Lopez-Opening-Old-Steinitz-Defense-4.Bxc6
Sicilian-Defense Sicilia

In [49]:
actual_stats['Game_type'].unique()

array(['blitz', 'bullet', 'rapid'], dtype=object)

In [50]:
actual_stats['Openings'].value_counts()

Sicilian-Defense             438
Kings-Pawn-Opening           117
Scotch-Game                   97
French-Defense                70
Philidor-Defense              68
Scandinavian-Defense          59
Queens-Pawn-Opening           49
Ruy-Lopez-Opening             33
Indian-Game                   32
Vant-Kruijs-Opening           23
Pirc-Defense                  22
Modern-Defense                18
Petrovs-Defense               17
Nimzowitsch-Defense           14
Kings-Fianchetto-Opening      13
Alekhines-Defense             12
Caro-Kann-Defense             12
Reti-Opening                  11
English-Opening                9
Benoni-Defense                 9
Nimzowitsch-Larsen-Attack      7
Mieses-Opening                 6
Englund-Gambit                 4
Grob-Opening                   4
Four-Knights-Game              4
Anderssen-Opening              3
Birds-Opening                  2
Italian-Game                   2
Kadas-Opening                  2
Vienna-Game                    1
Name: Open

In [51]:
games_df_dated=games_df

games_df_dated['date'].unique()

array(['03.25.2020', '03.21.2020', '03.20.2020', '03.19.2020',
       '03.17.2020', '03.05.2020', '03.02.2020', '03.01.2020',
       '02.29.2020', '02.27.2020', '02.25.2020', '02.24.2020',
       '02.23.2020', '02.22.2020', '02.21.2020', '02.20.2020',
       '02.19.2020', '02.16.2020', '02.15.2020', '02.14.2020',
       '02.13.2020', '02.12.2020', '02.09.2020', '02.08.2020',
       '02.07.2020', '02.06.2020', '02.05.2020', '02.01.2020',
       '01.31.2020', '01.30.2020', '01.29.2020', '01.28.2020',
       '01.27.2020', '01.26.2020', '01.25.2020', '01.24.2020',
       '01.23.2020', '01.22.2020', '01.21.2020', '01.20.2020',
       '01.19.2020', '01.18.2020', '01.17.2020', '01.16.2020',
       '01.15.2020', '01.14.2020', '01.13.2020', '01.12.2020',
       '01.11.2020', '01.10.2020', '01.09.2020', '01.08.2020',
       '01.07.2020', '01.06.2020', '01.05.2020', '01.04.2020',
       '01.03.2020', '01.02.2020', '01.01.2020'], dtype=object)

In [52]:
My_stats_dataset = pd.merge(games_df_final, actual_stats, on=['Api_url_key'], how='inner')

In [53]:
My_stats_dataset=My_stats_dataset.sort_values('date',ascending=True)
My_stats_dataset

index        date result  moves   speed  \
527    532  01.01.2020    win     16  10 min   
536    541  01.01.2020    win     33  10 min   
535    540  01.01.2020   loss     56  10 min   
534    539  01.01.2020   loss     21  10 min   
533    538  01.01.2020   loss     12  10 min   
..     ...         ...    ...    ...     ...   
539      2  03.25.2020   loss     12   1 min   
540      3  03.25.2020   draw     26   1 min   
6       11  03.25.2020    win     32   5 min   
537      0  03.28.2020   loss     24   1 min   
538      1  03.28.2020   loss     10   1 min   

                                                  link  my_elo  opponent_elo  \
527  https://www.chess.com/analysis/game/live/43561...    1228          1179   
536  https://www.chess.com/analysis/game/live/43552...    1241          1269   
535  https://www.chess.com/analysis/game/live/43558...    1233          1239   
534  https://www.chess.com/analysis/game/live/43559...    1226          1272   
533  https://www.chess.com/analysis/game/live/43559...    1218          1229   
..                                                 ...     ...           ...   
539  https://www.chess.com/analysis/game/live/46387...     855           817   
540  https://www.chess.com/analysis/game/live/46387...     864           906   
6    https://www.chess.com/analysis/game/live/46371...    1285          1205   
537  https://www.chess.com/analysis/game/live/46511...     839           900   
538  https://www.chess.com/analysis/game/live/46511...     846           816   

    opponent_country  opponent_name  ...  \
527       Azerbaijan        resn_01  ...   
536      Isle of Man  jeffchakamata  ...   
535      Netherlands      ziggy1961  ...   
534           Latvia      pavel-abc  ...   
533           Russia    Andrew72962  ...   
..               ...            ...  ...   
539            Nepal   Aarseusbeast  ...   
540            India     chears1105  ...   
6      International        Komodo9  ...   
537            India      Chaitu112  ...   
538            India         nils12  ...   

                                     Opening_variation First_move Second_move  \
527  Scandinavian-Defense-Mieses-Kotrc-Gubinsky-Mel...        e4          d5    
536             Sicilian-Defense-French-Variation-3.d4        e4          e6    
535                    Indian-Game-East-Indian-Defense        d4          e6    
534                     Sicilian-Defense-Closed-2...d6        e4          c5    
533  Sicilian-Defense-Smith-Morra-Gambit-Accepted-4...        e4          c5    
..                                                 ...        ...         ...   
539             Ruy-Lopez-Opening-Berlin-Defense-4.O-O        e4          e5    
540                    French-Defense-Knight-Variation        e4          e6    
6                      Indian-Game-East-Indian-Defense        d4          e6    
537                                   Sicilian-Defense        e4          c5    
538            Scotch-Game-3...exd4-4.Nxd4-Nxd4-5.Qxd4        e4          e5    

                 Openings My_color My_detailed_result  \
527  Scandinavian-Defense    white                win   
536      Sicilian-Defense    white                win   
535           Indian-Game    black         checkmated   
534      Sicilian-Defense    black           resigned   
533      Sicilian-Defense    black           resigned   
..                    ...      ...                ...   
539     Ruy-Lopez-Opening    white            timeout   
540        French-Defense    white         repetition   
6             Indian-Game    black                win   
537      Sicilian-Defense    black            timeout   
538           Scotch-Game    white           resigned   

    Opponent_detailed_result My_first_move Start_time  End_time  
527                 resigned           e4    16:28:05  16:31:50  
536                 resigned           e4    08:50:07  09:04:40  
535                      win           e6    14:25:49  14:45:52  
534             

In [54]:
for i in range(len(My_stats_dataset)):
    if (My_stats_dataset.loc[i,'Start_time'] >= '00:00:00' and My_stats_dataset.loc[i,'Start_time'] <= '01:00:00'):
          My_stats_dataset.at[i,'time_interval']= '12AM-1AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '01:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '02:00:00'):
          My_stats_dataset.at[i,'time_interval']= '1AM-2AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '02:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '03:00:00'):
          My_stats_dataset.at[i,'time_interval']= '2AM-3AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '03:00:00' and My_stats_dataset.loc[i,'Start_time'] <= '04:00:00'):
          My_stats_dataset.at[i,'time_interval']= '3AM-4AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '04:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '05:00:00'):
          My_stats_dataset.at[i,'time_interval']= '4AM-5AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '05:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '06:00:00'):
          My_stats_dataset.at[i,'time_interval']= '5AM-6AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '06:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '07:00:00'):
          My_stats_dataset.at[i,'time_interval']= '6AM-7AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '07:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '08:00:00'):
          My_stats_dataset.at[i,'time_interval']= '7AM-8AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '08:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '09:00:00'):
          My_stats_dataset.at[i,'time_interval']= '8AM-9AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '09:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '10:00:00'):
          My_stats_dataset.at[i,'time_interval']= '9AM-10AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '10:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '11:00:00'):
          My_stats_dataset.at[i,'time_interval']= '10AM-11AM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '11:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '12:00:00'):
          My_stats_dataset.at[i,'time_interval']= '11AM-12PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '12:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '13:00:00'):
          My_stats_dataset.at[i,'time_interval']= '12PM-1PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '13:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '14:00:00'):
          My_stats_dataset.at[i,'time_interval']= '1PM-2PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '14:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '15:00:00'):
          My_stats_dataset.at[i,'time_interval']= '2PM-3PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '15:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '16:00:00'):
          My_stats_dataset.at[i,'time_interval']= '3PM-4PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '16:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '17:00:00'):
          My_stats_dataset.at[i,'time_interval']= '4PM-5PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '17:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '18:00:00'):
          My_stats_dataset.at[i,'time_interval']= '5PM-6PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '18:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '19:00:00'):
          My_stats_dataset.at[i,'time_interval']= '6PM-7PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '19:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '20:00:00'):
          My_stats_dataset.at[i,'time_interval']= '7PM-8PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '20:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '21:00:00'):
          My_stats_dataset.at[i,'time_interval']= '8PM-9PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '21:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '22:00:00'):
          My_stats_dataset.at[i,'time_interval']= '9PM-10PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '22:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '23:00:00'):
          My_stats_dataset.at[i,'time_interval']= '10PM-11PM'
    elif (My_stats_dataset.loc[i,'Start_time'] >= '23:00:01' and My_stats_dataset.loc[i,'Start_time'] <= '24:00:00'):
          My_stats_dataset.at[i,'time_interval']= '11PM-12PM'


In [62]:
My_stats_dataset['Game_length_type']=My_stats_dataset['result']
for i in range(len(My_stats_dataset)):
    if My_stats_dataset.loc[i,'moves'] <=12: 
        My_stats_dataset.loc[i,'Game_length_type']='Opening_game'
    elif My_stats_dataset.loc[i,'moves'] >12 and My_stats_dataset.loc[i,'moves'] <=40:
        My_stats_dataset.loc[i,'Game_length_type']='Middle_game'
    else:
        My_stats_dataset.loc[i,'Game_length_type']='End_game'

In [63]:
My_stats_dataset

index        date result  moves   speed  \
527    532  01.01.2020    win     16  10 min   
536    541  01.01.2020    win     33  10 min   
535    540  01.01.2020   loss     56  10 min   
534    539  01.01.2020   loss     21  10 min   
533    538  01.01.2020   loss     12  10 min   
..     ...         ...    ...    ...     ...   
539      2  03.25.2020   loss     12   1 min   
540      3  03.25.2020   draw     26   1 min   
6       11  03.25.2020    win     32   5 min   
537      0  03.28.2020   loss     24   1 min   
538      1  03.28.2020   loss     10   1 min   

                                                  link  my_elo  opponent_elo  \
527  https://www.chess.com/analysis/game/live/43561...    1228          1179   
536  https://www.chess.com/analysis/game/live/43552...    1241          1269   
535  https://www.chess.com/analysis/game/live/43558...    1233          1239   
534  https://www.chess.com/analysis/game/live/43559...    1226          1272   
533  https://www.chess.com/analysis/game/live/43559...    1218          1229   
..                                                 ...     ...           ...   
539  https://www.chess.com/analysis/game/live/46387...     855           817   
540  https://www.chess.com/analysis/game/live/46387...     864           906   
6    https://www.chess.com/analysis/game/live/46371...    1285          1205   
537  https://www.chess.com/analysis/game/live/46511...     839           900   
538  https://www.chess.com/analysis/game/live/46511...     846           816   

    opponent_country  opponent_name  ... Second_move              Openings  \
527       Azerbaijan        resn_01  ...         d5   Scandinavian-Defense   
536      Isle of Man  jeffchakamata  ...         e6       Sicilian-Defense   
535      Netherlands      ziggy1961  ...         e6            Indian-Game   
534           Latvia      pavel-abc  ...         c5       Sicilian-Defense   
533           Russia    Andrew72962  ...         c5       Sicilian-Defense   
..               ...            ...  ...         ...                   ...   
539            Nepal   Aarseusbeast  ...         e5      Ruy-Lopez-Opening   
540            India     chears1105  ...         e6         French-Defense   
6      International        Komodo9  ...         e6            Indian-Game   
537            India      Chaitu112  ...         c5       Sicilian-Defense   
538            India         nils12  ...         e5            Scotch-Game   

    My_color My_detailed_result Opponent_detailed_result My_first_move  \
527    white                win                 resigned           e4    
536    white                win                 resigned           e4    
535    black         checkmated                      win           e6    
534    black           resigned                      win           c5    
533    black           resigned                      win           c5    
..       ...                ...                      ...           ...   
539    white            timeout                      win           e4    
540    white         repetition               repetition           e4    
6      black                win               checkmated           e6    
537    black            timeout                      win           c5    
538    white           resigned                      win           e4    

    Start_time  End_time time_interval Game_length_type  
527   16:28:05  16:31:50       4PM-5PM      Middle_game  
536   08:50:07  09:04:40       8AM-9AM      Middle_game  
535   14:25:49  14:45:52       2PM-3PM         End_game  
534   14:46:22  14:54:12       2PM-3PM      Middle_game  
533   14:54:20  14:56:33       2PM-3PM     Opening_game  
..         ...       ...           ...              ...  
539   05:45:10  05:46:54       5AM-6AM     Opening_game  
540   05:43:20  05:44:58       5AM-6AM      Middle_game  
6     19:39:13  19:43:48       7PM-8PM      Middle_game  
537   05:22:55  05:25:06       5AM-6AM      Middle_game  
538

In [55]:
grouped_multiple = My_stats_dataset.groupby(['time_interval']).agg({'time_interval': ['count']})
grouped_multiple.columns = ['time_interval_count']
grouped_multiple = grouped_multiple.reset_index()
grouped_multiple=grouped_multiple.dropna(how="any")
grouped_multiple=grouped_multiple.head(24)
(grouped_multiple)

time_interval  time_interval_count
0      10AM-11AM                   44
1      10PM-11PM                   29
2      11AM-12PM                   44
3      11PM-12PM                   15
4       12AM-1AM                    8
5       12PM-1PM                   49
6        1AM-2AM                   31
7        1PM-2PM                   61
8        2AM-3AM                   19
9        2PM-3PM                   43
10       3AM-4AM                   28
11       3PM-4PM                   64
12       4AM-5AM                   62
13       4PM-5PM                   48
14       5AM-6AM                   61
15       5PM-6PM                   53
16       6AM-7AM                   78
17       6PM-7PM                   44
18       7AM-8AM                  103
19       7PM-8PM                   29
20       8AM-9AM                   92
21       8PM-9PM                   51
22      9AM-10AM                   57
23      9PM-10PM                   51

In [56]:
grouped_multiple['time_interval_serial']=np.nan
for i in range(len(grouped_multiple)):
    if (grouped_multiple.loc[i,'time_interval'] == '12AM-1AM'):
        grouped_multiple.at[i,'time_interval_serial'] = 1
    elif (grouped_multiple.loc[i,'time_interval'] == '1AM-2AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 2
    elif (grouped_multiple.loc[i,'time_interval'] == '2AM-3AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 3
    elif (grouped_multiple.loc[i,'time_interval'] == '3AM-4AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 4
    elif (grouped_multiple.loc[i,'time_interval'] == '4AM-5AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 5
    elif (grouped_multiple.loc[i,'time_interval'] == '5AM-6AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 6
    elif (grouped_multiple.loc[i,'time_interval'] == '6AM-7AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 7
    elif (grouped_multiple.loc[i,'time_interval'] == '7AM-8AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 8
    elif (grouped_multiple.loc[i,'time_interval'] == '8AM-9AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 9
    elif (grouped_multiple.loc[i,'time_interval'] == '9AM-10AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 10
    elif (grouped_multiple.loc[i,'time_interval'] == '10AM-11AM'):
          grouped_multiple.at[i,'time_interval_serial'] = 11
    elif (grouped_multiple.loc[i,'time_interval'] == '11AM-12PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 12
    elif (grouped_multiple.loc[i,'time_interval'] == '12PM-1PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 13
    elif (grouped_multiple.loc[i,'time_interval'] == '1PM-2PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 14
    elif (grouped_multiple.loc[i,'time_interval'] == '2PM-3PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 15
    elif (grouped_multiple.loc[i,'time_interval'] == '3PM-4PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 16
    elif (grouped_multiple.loc[i,'time_interval'] == '4PM-5PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 17
    elif (grouped_multiple.loc[i,'time_interval'] == '5PM-6PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 18
    elif (grouped_multiple.loc[i,'time_interval'] == '6PM-7PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 19
    elif (grouped_multiple.loc[i,'time_interval'] == '7PM-8PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 20
    elif (grouped_multiple.loc[i,'time_interval'] == '8PM-9PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 21
    elif (grouped_multiple.loc[i,'time_interval'] == '9PM-10PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 22
    elif (grouped_multiple.loc[i,'time_interval'] == '10PM-11PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 23
    elif (grouped_multiple.loc[i,'time_interval'] == '11PM-12PM'):
          grouped_multiple.at[i,'time_interval_serial'] = 24

In [57]:
grouped_multiple=grouped_multiple.sort_values('time_interval_serial')
grouped_multiple

time_interval  time_interval_count  time_interval_serial
4       12AM-1AM                    8                   1.0
6        1AM-2AM                   31                   2.0
8        2AM-3AM                   19                   3.0
10       3AM-4AM                   28                   4.0
12       4AM-5AM                   62                   5.0
14       5AM-6AM                   61                   6.0
16       6AM-7AM                   78                   7.0
18       7AM-8AM                  103                   8.0
20       8AM-9AM                   92                   9.0
22      9AM-10AM                   57                  10.0
0      10AM-11AM                   44                  11.0
2      11AM-12PM                   44                  12.0
5       12PM-1PM                   49                  13.0
7        1PM-2PM                   61                  14.0
9        2PM-3PM                   43                  15.0
11       3PM-4PM                   64                  16.0
13       4PM-5PM                   48                  17.0
15       5PM-6PM                   53                  18.0
17       6PM-7PM                   44                  19.0
19       7PM-8PM                   29                  20.0
21       8PM-9PM                   51                  21.0
23      9PM-10PM                   51                  22.0
1      10PM-11PM                   29                  23.0
3      11PM-12PM                   15                  24.0

In [64]:
My_stats_dataset.to_csv(r'C:\chess_stats\My_stats_raw_bkp.csv', index = False)

In [ ]:
My_stats_dataset['Game_type'].value_counts()

In [ ]:
import urllib
import urllib.request

username = "JayJay1988" #change 
baseUrl = "https://api.chess.com/pub/player/" + username + "/games/"
archivesUrl = baseUrl + "archives"

#read the archives url and store in a list
f = urllib.request.urlopen(archivesUrl)
archives = f.read().decode("utf-8")
print(archives)
archives = archives.replace("{\"archives\":[\"", "\",\"")
archivesList = archives.split("\",\"" + baseUrl)
archivesList[len(archivesList)-1] = archivesList[len(archivesList)-1].rstrip("\"]}")
#print(archivesList)
#download all the archives
for i in range(len(archivesList)-1):
    url = baseUrl + archivesList[i+1] + "/pgn"
    filename = archivesList[i+1].replace("/", "-")
    print(filename)
    urllib.request.urlretrieve(url, "/MSBA/" + filename + ".pgn") #change
    print(filename + ".pgn has been downloaded.")
#print ("All files have been downloaded.")